In [1]:
%load_ext autoreload
%autoreload 2

In [2]:
import os
import sys
from pathlib import Path

# check if workding_dir is in local variables
if "workding_dir" not in locals():
    workding_dir = str(Path.cwd().parent)

os.chdir(workding_dir)
sys.path.append(workding_dir)
print("workding dir:", workding_dir)

workding dir: d:\code\projects\rapget-translation


In [3]:
from dotenv import find_dotenv, load_dotenv

found_dotenv = find_dotenv(".env")

if len(found_dotenv) == 0:
    found_dotenv = find_dotenv(".env.example")
print(f"loading env vars from: {found_dotenv}")
load_dotenv(found_dotenv, override=True)

loading env vars from: d:\code\projects\rapget-translation\.env


True

In [4]:
import os

model_name = os.getenv("MODEL_NAME")
adapter_name_or_path = os.getenv("ADAPTER_NAME_OR_PATH")
load_in_4bit = os.getenv("LOAD_IN_4BIT") == "true"
data_path = os.getenv("DATA_PATH")
results_path = os.getenv("RESULTS_PATH")
use_english_datasets = os.getenv("USE_ENGLISH_DATASETS") == "true"
max_new_tokens = int(os.getenv("MAX_NEW_TOKENS", 2048))

print(model_name, adapter_name_or_path, load_in_4bit, data_path, results_path, use_english_datasets, max_new_tokens)

01-ai/Yi-1.5-9B-Chat None True datasets/mac/mac.tsv results/mac-results_few_shots_4bit.csv False 300


In [5]:
%%time
os.environ["TOKENIZERS_PARALLELISM"] = "true"

!python --version
!pip show torch transformers

Python 3.11.9
Name: torch
Version: 2.4.0+cu124
Summary: Tensors and Dynamic neural networks in Python with strong GPU acceleration
Home-page: https://pytorch.org/
Author: PyTorch Team
Author-email: packages@pytorch.org
License: BSD-3
Location: C:\Users\dongh\.conda\envs\rapget\Lib\site-packages
Requires: filelock, fsspec, jinja2, networkx, sympy, typing-extensions
Required-by: accelerate, bitsandbytes, peft, torchaudio, torchvision
---
Name: transformers
Version: 4.43.3
Summary: State-of-the-art Machine Learning for JAX, PyTorch and TensorFlow
Home-page: https://github.com/huggingface/transformers
Author: The Hugging Face team (past and future) with the help of all our contributors (https://github.com/huggingface/transformers/graphs/contributors)
Author-email: transformers@huggingface.co
License: Apache 2.0 License
Location: C:\Users\dongh\.conda\envs\rapget\Lib\site-packages
Requires: filelock, huggingface-hub, numpy, packaging, pyyaml, regex, requests, safetensors, tokenizers, tqdm
R

In [6]:
from llm_toolkit.llm_utils import *
from llm_toolkit.translation_utils import *

device = check_gpu()

c:\Users\dongh\.conda\envs\rapget\Lib\site-packages\threadpoolctl.py:1214: RuntimeWarning: 
Found Intel OpenMP ('libiomp') and LLVM OpenMP ('libomp') loaded at
the same time. Both libraries are known to be incompatible and this
can cause random crashes or deadlocks on Linux when loaded in the
same Python program.
Using threadpoolctl may cause crashes or deadlocks. For more
information and possible workarounds, please see
    https://github.com/joblib/threadpoolctl/blob/master/multiple_openmp.md

  warnings.warn(msg, RuntimeWarning)
[nltk_data] Downloading package wordnet to
[nltk_data]     C:\Users\dongh\AppData\Roaming\nltk_data...
[nltk_data]   Package wordnet is already up-to-date!
[nltk_data] Downloading package punkt to
[nltk_data]     C:\Users\dongh\AppData\Roaming\nltk_data...
[nltk_data]   Package punkt is already up-to-date!
[nltk_data] Downloading package omw-1.4 to
[nltk_data]     C:\Users\dongh\AppData\Roaming\nltk_data...
[nltk_data]   Package omw-1.4 is already up-to-date

loading: d:\code\projects\rapget-translation\eval_modules\calc_repetitions.py
loading d:\code\projects\rapget-translation\llm_toolkit\translation_utils.py


[nltk_data] Downloading package wordnet to
[nltk_data]     C:\Users\dongh\AppData\Roaming\nltk_data...
[nltk_data]   Package wordnet is already up-to-date!
[nltk_data] Downloading package punkt to
[nltk_data]     C:\Users\dongh\AppData\Roaming\nltk_data...
[nltk_data]   Package punkt is already up-to-date!
[nltk_data] Downloading package omw-1.4 to
[nltk_data]     C:\Users\dongh\AppData\Roaming\nltk_data...
[nltk_data]   Package omw-1.4 is already up-to-date!


CUDA is available, we have found  1  GPU(s)
NVIDIA GeForce RTX 4080 Laptop GPU
CUDA version: 12.4


In [7]:
datasets = load_translation_dataset(data_path)

loading train/test data files
DatasetDict({
    train: Dataset({
        features: ['chinese', 'english'],
        num_rows: 4528
    })
    test: Dataset({
        features: ['chinese', 'english'],
        num_rows: 1133
    })
})


In [8]:
os.getenv("OPENAI_MODEL")
base_url = os.getenv("OPENAI_BASE_URL") or None

In [9]:
eval_dataset = datasets["test"].select([260, 908])
print_row_details(eval_dataset.to_pandas(), range(len(eval_dataset)))

--------------------------------------------------
chinese: 那刘姥姥先听见告艰苦，只当是没想头了， 又听见给他二十两银子，喜的眉开眼笑道：“我们也知道艰难的，但只俗语说的：‘瘦死的骆驼比马还大’呢。
--------------------------------------------------
english: When Grannie Liu heard Xi-feng talk about 'difficulties' she concluded that there was no hope. Her delight and the way in which her face lit up with pleasure when she heard that she was, after all, to be given twenty taels of silver can be imagined. 'We knew you had your troubles,' she said, 'but as the saying goes, 'A starved camel is bigger than a fat horse.'
--------------------------------------------------
chinese: 后来她不挣扎了，对我说，混蛋，你要把我怎么办。
--------------------------------------------------
english: After a while, she no longer struggled and said, You bastard! What are you going to do with me?


In [10]:
translation_prompt = get_few_shot_prompt(datasets["train"], num_shots=5)
print(translation_prompt)

You will be given a Chinese sentence to translate. If it is an incomplete sentence, or if you are unsure about the meaning, simply copy the input text as your output. Do not output any additional sentence such as explanation or reasoning.

Example Translations:
Chinese: 全仗着狐仙搭救。
English: Because I was protected by a fox fairy.
Chinese: 过后，表哥告诉她俩，这人是导演，在外国留过学的，还会编剧，今天拍的这戏，就是他自编自导的。
English: He was the director, the cousin later told them. He had studied abroad and was also a screenwriter; in fact he had written and directed the scene they had earlier seen being filmed.
Chinese: 这凤姐忽然想起一件事来，便向窗外叫：“蓉儿回来！”
English: Xi-feng suddenly seemed to remember something, and called to him through the window, 'Rong, come back!'
Chinese: 三个老红卫兵走到叶文洁面前，面对着她站成了一排——当年，她们也是这样面对叶哲泰的——试图再现那早已忘却的尊严，但她们当年那魔鬼般的精神力量显然已荡然无存。
English: The three old Red Guards stood in front of Ye in a row—just like they had stood against Ye Zhetai—trying to recapture their long-forgotten dignity. But the demonic spiritual energy 

In [11]:
from langchain_core.globals import set_debug

set_debug(True)

translate_via_openai(eval_dataset["chinese"][0], translation_prompt, max_tokens=max_new_tokens)

[chain/start] [chain:RunnableSequence] Entering Chain run with input:
{
  "input": "那刘姥姥先听见告艰苦，只当是没想头了， 又听见给他二十两银子，喜的眉开眼笑道：“我们也知道艰难的，但只俗语说的：‘瘦死的骆驼比马还大’呢。"
}
[chain/start] [chain:RunnableSequence > prompt:ChatPromptTemplate] Entering Prompt run with input:
{
  "input": "那刘姥姥先听见告艰苦，只当是没想头了， 又听见给他二十两银子，喜的眉开眼笑道：“我们也知道艰难的，但只俗语说的：‘瘦死的骆驼比马还大’呢。"
}
[chain/end] [chain:RunnableSequence > prompt:ChatPromptTemplate] s] Exiting Prompt run with output:
[outputs]
[llm/start] [chain:RunnableSequence > llm:ChatOpenAI] Entering LLM run with input:
{
  "prompts": [
    "System: You are a helpful assistant that translates Chinese to English.\nHuman: You will be given a Chinese sentence to translate. If it is an incomplete sentence, or if you are unsure about the meaning, simply copy the input text as your output. Do not output any additional sentence such as explanation or reasoning.\n\nExample Translations:\nChinese: 全仗着狐仙搭救。\nEnglish: Because I was protected by a fox fairy.\nChinese: 过后，表哥告诉她俩，这人是导演，在外国

'That Liu Laolao first heard about the hardships and thought it was hopeless, then heard about the twenty taels of silver and smiled with joy, saying, "We also know about difficulties, but as the saying goes: \'A dead camel is still bigger than a horse.\'"'

In [12]:
datasets["test"] = eval_dataset

In [13]:
predictions = eval_openai(5, datasets)

  0%|          | 0/2 [00:00<?, ?it/s]

[chain/start] [chain:RunnableSequence] Entering Chain run with input:
{
  "input": "那刘姥姥先听见告艰苦，只当是没想头了， 又听见给他二十两银子，喜的眉开眼笑道：“我们也知道艰难的，但只俗语说的：‘瘦死的骆驼比马还大’呢。"
}
[chain/start] [chain:RunnableSequence > prompt:ChatPromptTemplate] Entering Prompt run with input:
{
  "input": "那刘姥姥先听见告艰苦，只当是没想头了， 又听见给他二十两银子，喜的眉开眼笑道：“我们也知道艰难的，但只俗语说的：‘瘦死的骆驼比马还大’呢。"
}
[chain/end] [chain:RunnableSequence > prompt:ChatPromptTemplate] s] Exiting Prompt run with output:
[outputs]
[llm/start] [chain:RunnableSequence > llm:ChatOpenAI] Entering LLM run with input:
{
  "prompts": [
    "System: You are a helpful assistant that translates Chinese to English.\nHuman: You will be given a Chinese sentence to translate. If it is an incomplete sentence, or if you are unsure about the meaning, simply copy the input text as your output. Do not output any additional sentence such as explanation or reasoning.\n\nExample Translations:\nChinese: 全仗着狐仙搭救。\nEnglish: Because I was protected by a fox fairy.\nChinese: 过后，表哥告诉她俩，这人是导演，在外国

 50%|█████     | 1/2 [00:02<00:02,  2.31s/it]

[llm/end] [chain:RunnableSequence > llm:ChatOpenAI] [1.27s] Exiting LLM run with output:
{
  "generations": [
    [
      {
        "text": "That Liu Laolao first heard about the hardships and thought it was hopeless, then heard about the twenty taels of silver and smiled with joy, saying, \"We also know it's difficult, but as the saying goes: 'A dead camel is still bigger than a horse.'\"",
        "generation_info": {
          "finish_reason": "stop",
          "logprobs": null
        },
        "type": "ChatGeneration",
        "message": {
          "lc": 1,
          "type": "constructor",
          "id": [
            "langchain",
            "schema",
            "messages",
            "AIMessage"
          ],
          "kwargs": {
            "content": "That Liu Laolao first heard about the hardships and thought it was hopeless, then heard about the twenty taels of silver and smiled with joy, saying, \"We also know it's difficult, but as the saying goes: 'A dead camel is st

100%|██████████| 2/2 [00:04<00:00,  2.12s/it]

[llm/end] [chain:RunnableSequence > llm:ChatOpenAI] s] Exiting LLM run with output:
{
  "generations": [
    [
      {
        "text": "Later, she stopped struggling and said to me, \"Bastard, what are you going to do with me?\"",
        "generation_info": {
          "finish_reason": "stop",
          "logprobs": null
        },
        "type": "ChatGeneration",
        "message": {
          "lc": 1,
          "type": "constructor",
          "id": [
            "langchain",
            "schema",
            "messages",
            "AIMessage"
          ],
          "kwargs": {
            "content": "Later, she stopped struggling and said to me, \"Bastard, what are you going to do with me?\"",
            "response_metadata": {
              "token_usage": {
                "completion_tokens": 24,
                "prompt_tokens": 433,
                "total_tokens": 457
              },
              "model_name": "gpt-4o-mini-2024-07-18",
              "system_fingerprint": "fp_6

In [14]:
print(predictions)

['That Liu Laolao first heard about the hardships and thought it was hopeless, then heard about the twenty taels of silver and smiled with joy, saying, "We also know it\'s difficult, but as the saying goes: \'A dead camel is still bigger than a horse.\'"', 'Later, she stopped struggling and said to me, "Bastard, what are you going to do with me?"']


In [15]:
calc_metrics(eval_dataset["english"], predictions)

{'meteor': 0.5376810911615811,
 'bleu_scores': {'bleu': 0.16133991724232039,
  'precisions': [0.5454545454545454,
   0.26666666666666666,
   0.1643835616438356,
   0.09859154929577464],
  'brevity_penalty': 0.7322097138745853,
  'length_ratio': 0.7623762376237624,
  'translation_length': 77,
  'reference_length': 101},
 'rouge_scores': {'rouge1': 0.5594202898550725,
  'rouge2': 0.362051015096304,
  'rougeL': 0.5246376811594203,
  'rougeLsum': 0.5246376811594203},
 'accuracy': 0.0}